In [1]:
import numpy as np
from freetype import Face
import trimesh
from shapely import geometry
from objects.parameters import INTERFACE_WIDTH, LABEL_DEPTH
HEIGHT = 2200
WIDTH = 1600

def get_character_outline(char, shift = (0,0), scale = 1):
    assert len(char) == 1
    face = Face(r'C:\Windows\Fonts\consolab.ttf')
    face.set_char_size( 48*64 )  # If changing, must also change HEIGHT and WIDTH in calc_offsets
    face.load_char(char)
    slot = face.glyph
    outline = slot.outline
    contours = outline.contours

    # Iterate through contours to get groups of points
    start = 0
    contours_list = []
    outline_points = np.array(outline.points)
    outline_points += shift  # Shift x and y
    for c in contours:
        end = c+1
        contour_points = outline_points[start:end]
        contour_points = np.vstack([contour_points, contour_points[0]])
        contour_points = contour_points.astype('float')

        # Scale points to fit onto interface. Interface is 25.4mm in width. We partition that as if we have 6 characters per line (max is 5 in reality). 
        NUM_CHARS_PER_LINE_WITH_ADDITIONAL = 5
        scale = INTERFACE_WIDTH / (WIDTH * NUM_CHARS_PER_LINE_WITH_ADDITIONAL)
        contour_points *= scale
        contours_list.append(contour_points)
        start = end
    
    return contours_list


def calc_offsets(text):


    lines = text.split("\n")
    num_lines = len(lines)

    # Calculate height offsets based on number of lines
    height_offsets = np.arange(HEIGHT*num_lines,0,  -HEIGHT)
    if num_lines % 2 == 1:
        height_offsets -= height_offsets[(num_lines-1)//2] + HEIGHT//2
    else:
        height_offsets -= height_offsets[num_lines//2] + HEIGHT
        
    # Calculate width offsets based on number of charactes in each line
    offsets = []
    for line_num, line in enumerate(lines):
        num_chars = len(line)

        width_offsets = np.arange(0, WIDTH*num_chars, WIDTH )
        if num_chars % 2 == 1:
            width_offsets -= width_offsets[(num_chars)//2] + WIDTH//2
        else:
            width_offsets -= width_offsets[(num_chars)//2]

        line_offset = [(w, height_offsets[line_num]) for w in width_offsets]
        offsets.append(line_offset)

    # Traverse characters to output a nested list corresponding to offsets
    chars = []
    for line_num, line in enumerate(lines):
        char = [c for c in line]
        chars.append(char)

    return chars, offsets

def text_to_mesh(text, extrusion_height):


    # Extract characters and calculate offsets for centering lines/characters
    chars, offsets = calc_offsets(text)    
    
    # Gather outlines of characters
    text_list = []
    for line_num, line in enumerate(chars):
        
        assert len(line) <= 4, "No more than 4 characters allowed per line."
        for char_num, char in enumerate(line):
            
            offset = offsets[line_num][char_num]
            contours_list = get_character_outline(char, shift=offset)
            exterior = contours_list[0]
            num_contours = len(contours_list)
            
            if num_contours > 1:
                interior =contours_list[1:]
            else:
                interior = []

            text_list.append([exterior, interior])
    
    polygons = []
    for exterior, interior in text_list:
        polygons.append(geometry.Polygon(shell = exterior, holes = interior))

    import trimesh
    meshes = []
    for poly in polygons:
        meshes.append(trimesh.creation.extrude_polygon(poly, extrusion_height * 2))  # Double extrusion since half will not be intersecting the interface (i.e. need to double or else the actual depth of the label will not equal the requested depth).

    return meshes


text = "0\n5W89"
meshes = text_to_mesh(text, LABEL_DEPTH)
trimesh.Scene(meshes).show()


C:\Users\William\Anaconda3\envs\objects_venv_test\lib\site-packages\IPython\core\display.py:724: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


In [2]:
from objects.interface import Interface
from objects.parameters import INTERFACE_PATH, INTERFACE_WIDTH
interface = Interface(INTERFACE_PATH, label="test456")


In [3]:
from objects.utilities import calc_R_euler_angles

R = calc_R_euler_angles([ np.pi/2,0,3*np.pi/2])
goal_position = np.array([-INTERFACE_WIDTH/2 + LABEL_DEPTH , 0, -INTERFACE_WIDTH/2])
T = np.eye(4)
T[:3, :3] = R
T[:3, 3] = goal_position
new_meshes = [mesh.copy().apply_transform(T) for mesh in meshes]
trimesh.Scene([interface.mesh, *new_meshes]).show()


C:\Users\William\Anaconda3\envs\objects_venv_test\lib\site-packages\IPython\core\display.py:724: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


In [34]:
from objects.utilities import fuse_meshes,calc_mesh_boolean_and_edges


mesh1 = interface.mesh.copy()
for mesh2 in new_meshes:
    mesh1 = fuse_meshes(mesh1, mesh2, fairing_distance=0, operation='difference')   
    # union_mesh, edge_verts_indices = calc_mesh_boolean_and_edges(mesh1, mesh2, 'difference')
interface=mesh1

In [36]:
interface.show()

C:\Users\William\Anaconda3\envs\objects_venv_test\lib\site-packages\IPython\core\display.py:724: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


In [109]:

from objects.components import (
    sd_cylinder,
)
from objects.cross_section import CrossSection
from objects.axial_component import AxialComponent
from objects.shape import Shape
from objects.backbone import Backbone
from objects.utilities import transform_sd_mesh
from objects.parameters import cs_scale_backbone
c = np.cos
s = np.sin
base_cp_round = np.array(
    [
        [c(0 / 6 * 2 * np.pi), s(0 / 6 * 2 * np.pi)],
        [c(1 / 6 * 2 * np.pi), s(1 / 6 * 2 * np.pi)],
        [c(2 / 6 * 2 * np.pi), s(2 / 6 * 2 * np.pi)],
        [c(3 / 6 * 2 * np.pi), s(3 / 6 * 2 * np.pi)],
        [c(4 / 6 * 2 * np.pi), s(4 / 6 * 2 * np.pi)],
        [c(5 / 6 * 2 * np.pi), s(5 / 6 * 2 * np.pi)],
    ]
)

# Create base backbone
cp = np.array(
    [
        [0, 0, 0],
        [0, 10, 0],
        [0, 20, 0],
        [0, 30, 0],
        [10, 40, 0],
        [20, 50, 0],
        [30, 60, 0],
    ]
)
from objects.components import backbone_flat

sd_mesh, origin = sd_cylinder

ac = AxialComponent(
    backbone_flat, [CrossSection(base_cp_round * cs_scale_backbone, i) for i in np.linspace(0.1, 0.9, 5)]
)
s = Shape([ac])
theta_backbone = np.pi
theta_linear_segment = 3 * np.pi / 2
pos = 0.25
sd_mesh_transformed = transform_sd_mesh(sd_mesh, origin, ac, pos, theta_backbone, theta_linear_segment)
# sd_mesh_rotations = [transform_sd_mesh(sd_mesh, origin, ac, pos, theta_backbone, theta_linear_segment) for theta_linear_segment in np.linspace(0, 2*np.pi, 4, endpoint=False)]

s.combine_meshes([s.mesh, sd_mesh_transformed], operation="difference")
s.mesh.show(smooth=False)
sample_shape = s

In [124]:
POST_LENGTH = 10
POST_RADIUS = 7.5
POST_OFFSET = 5
new_interface = interface.copy()
dist_to_peg_tip = 0 #new_interface.vertices[:,0].min()  #
shape_min_x = 0 #sample_shape.mesh.vertices[:,0].min()
R = calc_R_euler_angles([ np.pi/2,np.pi,np.pi/2])
goal_position = np.array([-POST_LENGTH,0,0])
T = np.eye(4)
T[:3, :3] = R
T[:3, 3] = goal_position
new_interface = new_interface.apply_transform(T) 
trimesh.Scene([sample_shape.mesh,new_interface ]).show()

C:\Users\William\Anaconda3\envs\objects_venv_test\lib\site-packages\IPython\core\display.py:724: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


In [129]:
NUM_POST_SECTIONS= 89  # Certain values cause boolean errors
post = trimesh.creation.cylinder( POST_RADIUS,POST_LENGTH+POST_OFFSET, sections = NUM_POST_SECTIONS)
R = calc_R_euler_angles([ 0,np.pi/2,0])
goal_position = np.array([-(POST_LENGTH+POST_OFFSET/2)/2,0,0])#np.array([0,,0])
T = np.eye(4)
T[:3, :3] = R
T[:3, 3] = goal_position
post = post.apply_transform(T)
trimesh.Scene([sample_shape.mesh,new_interface , post ]).show(smooth=False)

In [130]:
fused_shape = new_interface
for mesh2 in [post, sample_shape.mesh]:
    if mesh2 == sample_shape.mesh:
        fairing_distance = 3
    else:
        fairing_distance = 0
    fused_shape = fuse_meshes(fused_shape, mesh2, fairing_distance, 'union')
fused_shape.show(smooth=False)

In [131]:
assert new_interface.is_watertight
assert post.is_watertight
fused_shape = fuse_meshes(new_interface, post, 0, 'union')
trimesh.repair.broken_faces(fused_shape, color=[255,0,0,0])
fused_shape.show(smooth=False)

In [96]:
x= sample_shape.mesh.bounds

In [98]:
x

array([[-17.49421488,   0.        , -17.31704397],
       [ 35.12073581,  65.12073581,  17.31704397]])